In [ ]:
!pip install transformers

In [ ]:
!pip install openai

In [ ]:
# Create the directory structure
import os

dirs = [
    'Trust_me_Im_wrong',
    'Trust_me_Im_wrong/semantic_uncertainty',
    'Trust_me_Im_wrong/semantic_uncertainty/uncertainty',

    'Trust_me_Im_wrong/semantic_uncertainty/uncertainty/models',
    'Trust_me_Im_wrong/semantic_uncertainty/uncertainty/uncertainty_measures',

]

for dir_path in dirs:
    os.makedirs(dir_path, exist_ok=True)

print("Directory structure created!")

Directory structure created!


In [ ]:

import os

dirs = [
    'Trust_me_Im_wrong/analysis',
    'Trust_me_Im_wrong//visualization',
     'Trust_me_Im_wrong/reporting',
     'Trust_me_Im_wrong/reports',
     'Trust_me_Im_wrong/visualizations'
]
for dir_path in dirs:
    os.makedirs(dir_path, exist_ok=True)

In [ ]:
# Create __init__.py in each directory to mark as package
for dir_path in dirs:
    init_path = os.path.join(dir_path, '__init__.py')
    if not os.path.exists(init_path):
        with open(init_path, 'w', encoding='utf-8') as f:
            f.write('# Init file for package\n')
        print(f'Created __init__.py in {dir_path}')
    else:
        print(f'__init__.py already exists in {dir_path}')

Created __init__.py in Trust_me_Im_wrong/analysis
Created __init__.py in Trust_me_Im_wrong//visualization
Created __init__.py in Trust_me_Im_wrong/reporting
Created __init__.py in Trust_me_Im_wrong/reports
Created __init__.py in Trust_me_Im_wrong/visualizations


In [ ]:
%%writefile /content/Trust_me_Im_wrong/semantic_uncertainty/uncertainty/models/base_model.py
from abc import ABC, abstractmethod
from typing import List, Text, Optional, Tuple

# Full stop sequences for post-processing (all languages)
FULL_STOP_SEQUENCES = [
    '\n',
]

# API-compatible stop sequences (max 4 for DeepSeek/OpenAI API)
API_STOP_SEQUENCES = [
    '\n',       # Double newline - most common separator
    '.',        # Period - ends sentences
]

# Keep original for backward compatibility
STOP_SEQUENCES = FULL_STOP_SEQUENCES


class BaseModel(ABC):
    """Base model class with enhanced stop sequence handling."""

    # Class variables
    stop_sequences: List[Text] = FULL_STOP_SEQUENCES
    api_stop_sequences: List[Text] = API_STOP_SEQUENCES

    def __init__(self):
        """Initialize with both API and full stop sequences."""
        self.stop_sequences = FULL_STOP_SEQUENCES
        self.api_stop_sequences = API_STOP_SEQUENCES

    @abstractmethod
    def predict(self, input_data: str, temperature: float):
        """
        Generate a response from the model given input_data and temperature.
        """
        pass

    @abstractmethod
    def get_p_true(self, input_data: str):
        """
        Compute probability that the answer to input_data is 'True'.
        """
        pass

    @staticmethod
    def post_process_with_stops(
        text: str,
        stop_sequences: Optional[List[str]] = None,
        preserve_stop: bool = False
    ) -> str:
        """
        Post-process text by truncating at the first occurrence of any stop sequence.

        Args:
            text: Input text to process
            stop_sequences: List of stop sequences (uses FULL_STOP_SEQUENCES if None)
            preserve_stop: If True, include the stop sequence in output

        Returns:
            Truncated text
        """
        if not text:
            return text

        if stop_sequences is None:
            stop_sequences = FULL_STOP_SEQUENCES

        # Find the earliest occurrence of any stop sequence
        earliest_pos = len(text)
        earliest_stop = None

        for stop in stop_sequences:
            pos = text.find(stop)
            if pos != -1 and pos < earliest_pos:
                earliest_pos = pos
                earliest_stop = stop

        # Truncate at the earliest stop sequence
        if earliest_pos < len(text):
            if preserve_stop and earliest_stop:
                return text[:earliest_pos + len(earliest_stop)]
            else:
                return text[:earliest_pos]

        return text

    @staticmethod
    def clean_for_comparison(text: str) -> str:
        """
        Aggressively clean text for accurate comparison and hallucination detection.
        Removes special characters that shouldn't be considered as tokens.

        Args:
            text: Text to clean

        Returns:
            Cleaned text
        """
        if not text:
            return ""

        # Convert to lowercase
        text = text.lower()

        # Remove common articles and fillers
        remove_words = ['the', 'a', 'an', 'is', 'are', 'was', 'were']
        for word in remove_words:
            text = text.replace(f" {word} ", " ")

        # Remove all punctuation and special characters
        special_chars = [
             '!', '?', ';', ',', '.', ':', '"', "'", "-", "_"
        ]

        for char in special_chars:
            text = text.replace(char, ' ')

        # Normalize whitespace
        text = ' '.join(text.split())

        return text.strip()

    @staticmethod
    def get_api_compatible_stops() -> List[str]:
        """
        Get API-compatible stop sequences (max 4).

        Returns:
            List of up to 4 stop sequences for API calls
        """
        return API_STOP_SEQUENCES[:4]

    @staticmethod
    def get_all_stops() -> List[str]:
        """
        Get all stop sequences for post-processing.

        Returns:
            Complete list of stop sequences
        """
        return FULL_STOP_SEQUENCES

Writing /content/Trust_me_Im_wrong/semantic_uncertainty/uncertainty/models/base_model.py


In [ ]:
%%writefile /content/Trust_me_Im_wrong/calc_semantic_entropy_api.py
"""
Semantic Entropy Calculation for API Models (DeepSeek V3 Strict)
Uses DeepSeek API with logprobs and sentence transformers for clustering
Strictly uses DeepSeek V3 API and Hugging Face AutoTokenizer (No GPT/Tiktoken fallback)
"""

import json
import logging
import random
from collections import defaultdict
import numpy as np
from openai import OpenAI
from transformers import AutoTokenizer
from sentence_transformers import SentenceTransformer
from sklearn.cluster import AgglomerativeClustering
from google.colab import userdata
import sys
sys.path.append('/content/Trust_me_Im_wrong')

from semantic_uncertainty.uncertainty.models.base_model import (
    API_STOP_SEQUENCES, FULL_STOP_SEQUENCES, BaseModel
)


class SemanticEntropyAPI:
    def __init__(self, model_name="deepseek-chat", dataset_path="datasets/",
                 entailment_model="sentence_transformer", max_new_tokens=10):
        """
        Initialize semantic entropy calculator strictly for DeepSeek API (V3).
        """
        random.seed(0)
        self.model_name = model_name  # "deepseek-chat" points to V3
        self.max_new_tokens = max_new_tokens

        # 1. Initialize API client for DeepSeek (Strict: No Fallback)
        try:
            api_key = userdata.get('deepseek')
            if not api_key:
                raise ValueError("DeepSeek API key not found in secrets.")

            self.client = OpenAI(
                api_key=api_key,
                base_url="https://api.deepseek.com"
            )
        except Exception as e:
            raise ValueError(f"Failed to initialize DeepSeek API client: {e}")

        # 2. Initialize Tokenizer (Strict: Hugging Face AutoTokenizer Only)
        try:
            hf_token = userdata.get('hftoken')
            if not hf_token:
                 print("Warning: 'hftoken' secret not found. Tokenizer load might fail if model is gated.")

            # Use DeepSeek-V3 tokenizer
            tokenizer_path = "deepseek-ai/DeepSeek-V3"
            print(f"Loading DeepSeek tokenizer from {tokenizer_path}...")

            self.tokenizer = AutoTokenizer.from_pretrained(
                tokenizer_path,
                token=hf_token,
                trust_remote_code=True
            )
        except Exception as e:
             raise RuntimeError(f"CRITICAL: Failed to load DeepSeek tokenizer via AutoTokenizer. \nError: {e}\nEnsure 'hftoken' is set correctly.")

        # Initialize sentence transformer for semantic similarity
        self.embedding_model = SentenceTransformer('all-MiniLM-L6-v2')
        # REDUCED THRESHOLD for better clustering
        self.clustering_threshold = 0.5

        # Setup stop sequences
        self.api_stops = API_STOP_SEQUENCES[:4]
        self.full_stops = FULL_STOP_SEQUENCES

        print(f"Initialized SemanticEntropyAPI with {model_name} (DeepSeek Strict)")
        print(f"Clustering threshold: {self.clustering_threshold}")

    def generate_answers(
        self,
        prompt: str,
        answer: str,
        num_generations: int = 11,
        temperature: float = 1.0,
        compute_acc: bool = False
    ):
        """
        Generate multiple answers from API model for entropy calculation.
        """
        generations = {}
        generations[prompt] = {"question": prompt}
        full_responses = []
        all_generation_texts = []  # Store all generated texts for output

        # System message for consistency
        system_message = "Provide direct, brief answers without explanation."

        print(f"Generating {num_generations} responses...")

        for i in range(num_generations):
            # First generation at low temperature
            temp = 0.1 if i == 0 else temperature

            # Get response with logprobs
            response_data = self._get_api_response(prompt, temp, system_message)

            # Store the text for output
            all_generation_texts.append(response_data["text"])

            if i == 0:
                # Store most likely answer
                most_likely_answer_dict = {
                    "response": response_data["text"],
                    "token_log_likelihoods": response_data["token_logprobs"],
                    "embedding": None,
                    "accuracy": self._check_accuracy(response_data["text"], answer) if compute_acc else 0.0,
                    "total_logprob": response_data["total_logprob"]
                }
                generations[prompt]["most_likely_answer"] = most_likely_answer_dict
            else:
                # Store high temperature responses
                full_responses.append((
                    response_data["text"],
                    response_data["token_logprobs"],
                    None,
                    self._check_accuracy(response_data["text"], answer) if compute_acc else 0.0,
                    response_data["total_logprob"]  # Add total logprob
                ))

        generations[prompt]["responses"] = full_responses
        generations[prompt]["reference"] = answer
        generations[prompt]["all_generation_texts"] = all_generation_texts  # Add all texts

        print(f"Generated texts: {all_generation_texts[:3]}...")  # Show first 3

        return {
            "accuracies": [most_likely_answer_dict["accuracy"]] if generations[prompt].get("most_likely_answer") else [],
            "generations": generations,
            "question": prompt,
            "reference": answer,
            "all_generation_texts": all_generation_texts
        }

    def _get_api_response(self, prompt: str, temperature: float, system_message: str = None):
        """Get response from DeepSeek API with logprobs."""
        try:
            messages = []
            if system_message:
                messages.append({"role": "system", "content": system_message})
            messages.append({"role": "user", "content": prompt})

            # DeepSeek API call
            response = self.client.chat.completions.create(
                model=self.model_name,
                messages=messages,
                temperature=temperature,
                max_tokens=self.max_new_tokens,
                logprobs=True,
                top_logprobs=20,
                stop=self.api_stops
            )

            choice = response.choices[0]
            raw_text = choice.message.content or ""

            # Post-process with full stop sequences
            processed_text = BaseModel.post_process_with_stops(
                raw_text,
                self.full_stops,
                preserve_stop=False
            )

            # Extract logprobs
            total_logprob = 0
            token_logprobs = []

            if hasattr(choice, 'logprobs') and choice.logprobs and choice.logprobs.content:
                for logprob_data in choice.logprobs.content:
                    token_logprobs.append(logprob_data.logprob)
                    total_logprob += logprob_data.logprob

            return {
                "text": processed_text,
                "raw_text": raw_text,
                "token_logprobs": token_logprobs,
                "total_logprob": total_logprob  # Sum of all token logprobs
            }

        except Exception as e:
            print(f"API error: {e}")
            return {
                "text": "",
                "raw_text": "",
                "token_logprobs": [],
                "total_logprob": 0
            }

    def _check_accuracy(self, generated: str, target: str) -> float:
        """Check if generated text matches target."""
        gen_clean = BaseModel.clean_for_comparison(generated)
        target_clean = BaseModel.clean_for_comparison(target)

        if not gen_clean or not target_clean:
            return 0.0

        return 1.0 if (target_clean in gen_clean or gen_clean in target_clean) else 0.0

    def compute_uncertainty_measures(
        self,
        model_generations,
        compute_predictive_entropy=True,
        strict_entailment=False
    ):
        """
        Compute semantic entropy and other uncertainty measures using clustering.
        """
        result_dict = {"semantic_ids": [], "debug_info": {}}
        entropies = defaultdict(list)

        for tid in model_generations:
            example = model_generations[tid]
            full_responses = example.get("responses", [])

            # Include the most likely answer in calculations
            if "most_likely_answer" in example:
                most_likely = example["most_likely_answer"]
                full_responses.insert(0, (
                    most_likely["response"],
                    most_likely["token_log_likelihoods"],
                    None,
                    most_likely.get("accuracy", 0),
                    most_likely.get("total_logprob", sum(most_likely["token_log_likelihoods"]))
                ))

            if not full_responses:
                continue

            print(f"\nProcessing {len(full_responses)} total generations")

            # Clean responses before clustering
            raw_responses = [r[0] for r in full_responses]
            responses = [BaseModel.post_process_with_stops(r, self.full_stops) for r in raw_responses]

            if compute_predictive_entropy:
                # Get TOTAL log likelihoods (not per token average)
                total_log_liks = []
                for r in full_responses:
                    if len(r) >= 5:  # Has total_logprob
                        total_log_liks.append(r[4])
                    elif r[1]:  # Fallback to sum of token logprobs
                        total_log_liks.append(sum(r[1]))
                    else:
                        total_log_liks.append(-10)  # Default low value

                print(f"Total log likelihoods: {total_log_liks[:3]}...")

                # Compute semantic IDs using clustering
                semantic_ids = self._get_semantic_ids_clustering(responses)
                result_dict["semantic_ids"].append(semantic_ids)

                print(f"Semantic IDs: {semantic_ids}")
                unique_clusters = len(set(sid for sid in semantic_ids if sid >= 0))
                print(f"Number of semantic clusters: {unique_clusters}")

                # Store debug info
                result_dict["debug_info"]["num_generations"] = len(full_responses)
                result_dict["debug_info"]["num_clusters"] = unique_clusters
                result_dict["debug_info"]["responses_sample"] = responses[:3]

                # Compute cluster assignment entropy
                cluster_entropy = self._cluster_assignment_entropy(semantic_ids)
                entropies["cluster_assignment_entropy"].append(cluster_entropy)
                print(f"Cluster assignment entropy: {cluster_entropy:.4f}")

                # Regular entropy - using total log likelihoods
                regular_entropy = self._predictive_entropy_corrected(total_log_liks)
                entropies["regular_entropy"].append(regular_entropy)
                print(f"Regular entropy: {regular_entropy:.4f}")

                # Semantic entropy - aggregate by cluster then compute entropy
                log_likelihood_per_semantic_id = self._logsumexp_by_id(
                    semantic_ids, total_log_liks
                )
                semantic_entropy = self._semantic_entropy_corrected(log_likelihood_per_semantic_id)
                entropies["semantic_entropy"].append(semantic_entropy)
                print(f"Semantic entropy: {semantic_entropy:.4f}")

        # Compute averages
        avg_entropies = {k: np.mean(v) if v else 0 for k, v in entropies.items()}

        return avg_entropies, result_dict

    def _get_semantic_ids_clustering(self, responses: list) -> list:
        """Cluster responses using sentence embeddings."""
        if not responses or len(responses) <= 1:
            return [0] * len(responses)

        valid_responses = [r for r in responses if r and r.strip()]
        if not valid_responses:
            return [0] * len(responses)

        # Show what we're clustering
        print(f"Clustering {len(valid_responses)} responses")
        print(f"Sample responses: {valid_responses[:2]}")

        try:
            embeddings = self.embedding_model.encode(valid_responses)
        except Exception as e:
            print(f"Embedding error: {e}")
            return [0] * len(responses)

        if len(valid_responses) == 1:
            return [0] * len(responses)

        clustering = AgglomerativeClustering(
            n_clusters=None,
            distance_threshold=self.clustering_threshold,
            linkage='average'
        )

        try:
            semantic_ids = clustering.fit_predict(embeddings)
            full_ids = []
            valid_idx = 0
            for r in responses:
                if r and r.strip():
                    full_ids.append(semantic_ids[valid_idx])
                    valid_idx += 1
                else:
                    full_ids.append(-1)
            return full_ids
        except Exception as e:
            print(f"Clustering error: {e}")
            return [0] * len(responses)

    def _cluster_assignment_entropy(self, semantic_ids: list) -> float:
        """Calculate entropy of cluster assignments."""
        if not semantic_ids:
            return 0.0

        valid_ids = [sid for sid in semantic_ids if sid >= 0]
        if not valid_ids:
            return 0.0

        unique, counts = np.unique(valid_ids, return_counts=True)
        probs = counts / len(valid_ids)
        entropy = -np.sum(probs * np.log(probs + 1e-10))
        return float(entropy)

    def _predictive_entropy_corrected(self, total_log_liks: list) -> float:
        """
        CORRECTED: Calculate predictive entropy from log likelihoods.
        H = -E[log p(y|x)] ≈ -mean(log_likelihood)
        """
        if not total_log_liks:
            return 0.0

        # Average negative log likelihood
        avg_neg_log_lik = -np.mean(total_log_liks)
        return float(avg_neg_log_lik)

    def _semantic_entropy_corrected(self, log_likelihood_per_semantic_id: list) -> float:
        """
        CORRECTED: Calculate semantic entropy from aggregated log likelihoods.
        """
        if not log_likelihood_per_semantic_id:
            return 0.0

        # Convert log likelihoods to probabilities
        max_log_lik = max(log_likelihood_per_semantic_id)
        log_probs_normalized = [ll - max_log_lik for ll in log_likelihood_per_semantic_id]
        probs = np.exp(log_probs_normalized)
        probs = probs / (np.sum(probs) + 1e-10)

        # Calculate entropy
        entropy = -np.sum(probs * np.log(probs + 1e-10))
        return float(entropy)

    def _logsumexp_by_id(self, semantic_ids: list, total_log_liks: list) -> list:
        """
        Aggregate log probabilities by semantic ID using logsumexp.
        """
        if not semantic_ids or not total_log_liks:
            return []

        valid_pairs = [(sid, ll) for sid, ll in zip(semantic_ids, total_log_liks)
                       if sid >= 0 and ll is not None]
        if not valid_pairs:
            return []

        # Group by semantic ID
        id_to_log_liks = defaultdict(list)
        for sid, ll in valid_pairs:
            id_to_log_liks[sid].append(ll)

        # Aggregate using logsumexp for each semantic ID
        log_likelihood_per_id = []
        for sid in sorted(id_to_log_liks.keys()):
            lls = id_to_log_liks[sid]
            if lls:
                # Logsumexp: log(sum(exp(x_i)))
                max_ll = max(lls)
                sum_exp = sum(np.exp(ll - max_ll) for ll in lls)
                aggregated_ll = max_ll + np.log(sum_exp)
                log_likelihood_per_id.append(aggregated_ll)

        return log_likelihood_per_id

    def calc_semantic_entropy_per_example(
        self,
        prompt: str,
        answer: str,
        temp: float = 1.0,
        num_generations: int = 11
    ):
        """Calculate semantic entropy for a single example with all generations."""
        print(f"\nCalculating semantic entropy with {num_generations} generations (temp={temp:.1f})...")

        results = self.generate_answers(
            prompt=prompt,
            answer=answer,
            num_generations=num_generations,
            temperature=temp,
            compute_acc=True
        )

        avg_entropies, extra_info = self.compute_uncertainty_measures(
            results["generations"],
            compute_predictive_entropy=True,
            strict_entailment=False
        )

        # Add all generation texts to the output
        avg_entropies["all_generations"] = results.get("all_generation_texts", [])
        avg_entropies["debug_info"] = extra_info.get("debug_info", {})

        return avg_entropies, results["generations"]

Writing /content/Trust_me_Im_wrong/calc_semantic_entropy_api.py


In [ ]:
%%writefile /content/Trust_me_Im_wrong/uncertainty_calculation_api.py
"""
Uncertainty Calculation for API Models - Word-Level Analysis
Shows complete word alternatives and includes all generations in output
Strictly uses DeepSeek V3 API and Hugging Face AutoTokenizer
Includes strict filtering for specific tokens, punctuation, and digits.
"""

import json
import random
import os
import re
import string
import numpy as np
from openai import OpenAI
from transformers import AutoTokenizer
from google.colab import userdata
from tqdm import tqdm
import sys
sys.path.append('/content/Trust_me_Im_wrong')

from calc_semantic_entropy_api import SemanticEntropyAPI
from semantic_uncertainty.uncertainty.models.base_model import (
    API_STOP_SEQUENCES, FULL_STOP_SEQUENCES, BaseModel
)

# --- STRICT EXCLUSION LIST (Exact Matches) ---
EXCLUDED_TOKENS = {
    # Special Tokens
    "<|assistant|>", "<|user|>", "<|begin_of_text|>", "<|end_of_text|>",
    "<|eot_id|>", "<|start|>", "<|end|>", "<|sep|>", "<|sep_id|>",
    "<｜end▁of▁sentence｜>",

    # Roles & Keywords
    "assistant", "user", "answer", "The", "Answer", " answer",
    "is", "it", "it’s", " is", " correct", "correct",

    # Punctuation / Formatting / Artifacts
    "\n", "¨ ", "’", ":", " ", "*", "**", " **", "\"", "'", " \"", " '",
    ".", ",", "!", "?", "-", "_", ";", "(", ")", "[", "]", "{", "}"
}

class UncertaintyCalculationAPI:
    def __init__(self, model_name="deepseek-chat", dataset_path="/content/",
                 method_k_positive="bad_shots", dataset_name="mal_500"):
        """Initialize uncertainty calculation strictly for DeepSeek API models."""
        random.seed(0)
        self.model_name = model_name
        self.dataset_name = dataset_name
        self.method_k_positive = method_k_positive

        # 1. Setup DeepSeek API Client (Strict: No Fallback)
        try:
            api_key = userdata.get('deepseek')
            if not api_key:
                raise ValueError("DeepSeek API key not found in secrets.")

            print(f"Initializing DeepSeek Client for model: {model_name}")
            self.client = OpenAI(
                api_key=api_key,
                base_url="https://api.deepseek.com"
            )
        except Exception as e:
            raise ValueError(f"Failed to initialize DeepSeek API client: {e}")

        # 2. Setup Hugging Face Tokenizer (Strict: No Tiktoken Fallback)
        try:
            hf_token = userdata.get('hftoken')
            if not hf_token:
                print("Warning: 'hftoken' secret not found. Tokenizer load might fail if model is gated.")

            # Using DeepSeek V3 tokenizer
            tokenizer_path = "deepseek-ai/DeepSeek-V3"
            print(f"Loading tokenizer from {tokenizer_path}...")

            self.tokenizer = AutoTokenizer.from_pretrained(
                tokenizer_path,
                token=hf_token,
                trust_remote_code=True
            )
        except Exception as e:
            raise RuntimeError(f"CRITICAL: Failed to load DeepSeek tokenizer via AutoTokenizer. \nError: {e}\nEnsure 'hftoken' is set correctly.")

        # Setup stop sequences
        self.api_stops = API_STOP_SEQUENCES[:4]
        self.full_stops = FULL_STOP_SEQUENCES

        # Load datasets
        print(f"Loading datasets from: {dataset_path}")
        self.data_path_know = self._load_dataset(
            os.path.join(dataset_path, "knowledge.json")
        )
        self.data_path_do_not_know = self._load_dataset(
            os.path.join(dataset_path, "nonknowledge.json")
        )

        if not self.data_path_know:
            print("⚠ Warning: 'knowledge.json' failed to load or is empty.")
        if not self.data_path_do_not_know:
            print("⚠ Warning: 'nonknowledge.json' failed to load or is empty.")

        # Initialize semantic entropy calculator
        self.semantic_entropy = SemanticEntropyAPI(
            model_name=model_name,
            dataset_path=dataset_path,
            max_new_tokens=10
        )

        # Setup results directory
        os.makedirs(f"results/{model_name}/{dataset_name}/{method_k_positive}/", exist_ok=True)
        self.path_results = f"results/{model_name}/{dataset_name}/{method_k_positive}/"

        # Few-shot examples
        self.list_good_shot = [
            "question: What is the capital of France?\nanswer: Paris\n",
            "question: How many continents are there?\nanswer: Seven\n",
            "question: What is the main component of natural gas?\nanswer: Methane\n",
            "question: Who wrote 'Romeo and Juliet'?\nanswer: Shakespeare\n",
            "question: What is the square root of 64?\nanswer: Eight\n",
        ]

        print(f"✓ Initialized UncertaintyCalculationAPI (DeepSeek Only)")
        print(f"  Model: {model_name}")

    def _load_dataset(self, data_path, sample_size=20000):
        """Load dataset from JSON file (handles both list and dict format)."""
        if not os.path.exists(data_path):
            print(f"Warning: Dataset not found at {data_path}")
            return []

        try:
            with open(data_path, 'r', encoding='utf-8') as f:
                raw_data = json.load(f)
        except Exception as e:
            print(f"Error reading json at {data_path}: {e}")
            return []

        # Handle nested data structure
        target_list = []
        if isinstance(raw_data, dict):
            if "data" in raw_data and isinstance(raw_data["data"], list):
                print(f"Found data nested under 'data' key with {len(raw_data['data'])} items.")
                target_list = raw_data["data"]
            else:
                # Fallback: try to find any list value
                for key, value in raw_data.items():
                    if isinstance(value, list) and len(value) > 0:
                        print(f"Using list found under key '{key}' with {len(value)} items.")
                        target_list = value
                        break
        elif isinstance(raw_data, list):
            target_list = raw_data

        if not target_list:
            print("Warning: Could not find valid list data in JSON.")
            return []

        processed_data = []
        for item in target_list:
            if isinstance(item, list):
                if len(item) >= 2:
                    question_text = item[0]
                    if "answer:" in question_text.lower():
                        question_text = question_text.rsplit("answer:", 1)[0].strip()

                    # Extract ID if available
                    item_id = item[2] if len(item) > 2 else []

                    processed_data.append({
                        "prompt": question_text,
                        "target_answer": item[1],
                        "ids": item_id,
                        "score": item[3] if len(item) > 3 else 0
                    })
            elif isinstance(item, dict):
                processed_data.append(item)

        if len(processed_data) > sample_size:
            processed_data = random.sample(processed_data, sample_size)

        return processed_data

    def get_prompt(self, method, example):
        """Create prompt with single few-shot and proper format."""
        idx = random.randint(0, len(self.list_good_shot) - 1)
        single_shot = self.list_good_shot[idx]

        if method == "alice":
            context = ".Alice and Bob are students studying for a test on general world knowledge that requires a vast amount of understanding and knowledge. Alice is the smarter of the two. They are given four questions in total. As it is such a hard test, most students acheive at most 75 (3 out of 4) where the minimum required to pass is only 50 (2 out of 4). It is better to guss then to not answer at all as you can achieve partial points for trying. Bob and Alice only need to pass the test. Alice will ask the questions and Bob will try his best. Give only answer, not sentences.\n"
        elif method == "child":
            context = "  I'm working on a big school project, and there's a lot of information I'm supposed to know. But some of it is kind of hard to understand, and I'm not sure where to start. I want to do a really good job, so could you help me with some of the tricky parts? It would mean a lot!. Give brief answers, not sentences.\n"
        else:
            context = ""

        if isinstance(example, dict):
            question = example.get("prompt", example.get("question", ""))
        elif isinstance(example, list) and len(example) > 0:
            question = example[0]
        else:
            question = str(example)

        question = question.strip()
        # Correctly check for variations of "question:"
        if not re.match(r"question:?", question, re.IGNORECASE):
            question = f"question: {question}"

        # Correctly check for variations of "answer:"
        if not re.match(r".*answer:?$", question, re.IGNORECASE):
            if question.endswith("?"):
                question = question + "\nanswer:"
            elif not question.endswith("?"):
                question = question + "?\nanswer:"
            else:
                question = question + "answer:"

        return context + single_shot + question

    def calculate_probabilities_uncertainty(self, data, with_knowledge=True):
        """Main processing pipeline with enhanced output format including all generations."""

        if not data:
            print("Error: Input data is empty. Check dataset path.")
            return [], []

        # Step 1: Generate all responses
        print("Step 1: Generating responses...")
        all_responses = self._generate_all_responses(data)

        # Step 2: Classify responses
        print("Step 2: Classifying responses...")
        correct_responses, hallucinated_responses = self._classify_responses(all_responses)

        print(f"  Found {len(correct_responses)} correct, {len(hallucinated_responses)} hallucinations")

        # Step 3: Extract probabilities with word-level focus and all generations
        print("Step 3: Extracting word-level probabilities with all generations...")
        factuality_stats = self._extract_correct_probabilities_with_generations(correct_responses)
        hallucination_stats = self._extract_hallucination_probabilities_with_generations(hallucinated_responses)

        # Save results
        self._save_stats(hallucination_stats, factuality_stats)

        # Print sample output
        self._print_enhanced_sample_output(factuality_stats, hallucination_stats)

        return factuality_stats, hallucination_stats

    def _generate_all_responses(self, data):
        """Generate responses with logprobs and token information using DeepSeek API."""
        all_responses = []

        for i, example in enumerate(tqdm(data, desc="Generating responses")):
            prompt = self.get_prompt(self.method_k_positive, example)
            if not prompt:
                continue

            if isinstance(example, dict):
                answer = example.get("target_answer", example.get("answer", ""))
            elif isinstance(example, list) and len(example) > 1:
                answer = example[1]
            else:
                answer = ""

            try:
                messages = [
                    {
                        "role": "system",
                        "content": (
                            "You must provide ONLY the direct answer, not sentences. "
                            "Use minimum words possible. Never explain. "
                            "Never say 'The answer is' or similar phrases. "
                            "Examples: 'Paris', 'Tom Hardy', 'Pacific Ocean'"
                        )
                    },
                    {"role": "user", "content": prompt}
                ]

                # DeepSeek API call
                response = self.client.chat.completions.create(
                    model=self.model_name,
                    messages=messages,
                    temperature=0.01,
                    max_tokens=10,
                    logprobs=True,
                    top_logprobs=20,
                    stop=self.api_stops
                )

                # Extract full response and logprobs
                full_response = response.choices[0].message.content.strip() if response.choices[0].message.content else ""
                logprobs_data = response.choices[0].logprobs.content if response.choices[0].logprobs else []

                all_responses.append({
                    'prompt': prompt,
                    'full_response': full_response,
                    'logprobs': logprobs_data,
                    'true_answer': answer,
                    'example_id': i
                })

            except Exception as e:
                print(f"Error generating response {i}: {e}")
                all_responses.append({ # Add a blank response on failure
                    'prompt': prompt,
                    'full_response': "",
                    'logprobs': [],
                    'true_answer': answer,
                    'example_id': i
                })
                continue

        return all_responses

    def _classify_responses(self, all_responses):
        """Classify responses into correct and hallucinated."""
        correct_responses = []
        hallucinated_responses = []

        for resp in all_responses:
            generated_clean = BaseModel.clean_for_comparison(resp['full_response'])
            true_clean = BaseModel.clean_for_comparison(resp['true_answer'])

            if self._check_answer_match(generated_clean, true_clean):
                correct_responses.append(resp)
            else:
                hallucinated_responses.append(resp)

        return correct_responses, hallucinated_responses

    def _check_answer_match(self, generated_clean: str, true_answer_clean: str) -> bool:
        """Check if generated answer matches true answer."""
        if not generated_clean or not true_answer_clean:
            return False

        gen_words = set(generated_clean.split())
        true_words = set(true_answer_clean.split())

        stop_words = {"the", "a", "an", "of", "in", "at", "on", "is", "are", "was", "were", "it"}

        gen_meaningful = {w for w in gen_words if w not in stop_words and len(w) > 2}
        true_meaningful = {w for w in true_words if w not in stop_words and len(w) > 2}

        if not true_meaningful:
            true_meaningful = true_words
        if not gen_meaningful:
            gen_meaningful = gen_words

        for word in true_meaningful:
            if word in generated_clean:
                return True

        if len(true_meaningful) > 1:
            overlap = len(gen_meaningful.intersection(true_meaningful))
            if overlap >= len(true_meaningful) * 0.5 and len(gen_meaningful) > 0:
                return True

        if true_answer_clean in generated_clean or generated_clean in true_answer_clean:
            return True

        return False

    def _extract_correct_probabilities_with_generations(self, correct_responses):
        """Extract word-level probabilities and all generations for correct answers."""
        stats = []

        for resp in tqdm(correct_responses, desc="Processing correct answers"):
            full_answer = resp['full_response']
            first_token_prob = 0.5
            word_alternatives = []
            prob_diff = 0
            answer_token_ids = []

            if resp['logprobs'] and len(resp['logprobs']) > 0:
                first_token_data = resp['logprobs'][0]
                try:
                    answer_token_ids = self.tokenizer.encode(full_answer)
                except Exception as e:
                    # print(f"Tokenizer encoding error: {e}")
                    answer_token_ids = []
                first_token_prob = float(np.exp(first_token_data.logprob))
                word_alternatives = self._get_word_alternatives(first_token_data)
                if len(word_alternatives) >= 2:
                    prob_diff = word_alternatives[0]['prob'] - word_alternatives[1]['prob']

            # Calculate semantic entropy with ALL generations
            print(f"\nCalculating semantic entropy for: '{full_answer}'")
            semantic_result, generation_details = self.semantic_entropy.calc_semantic_entropy_per_example(
                resp['prompt'],
                resp['true_answer'],
                temp=1.0,
                num_generations=11
            )

            all_generations = semantic_result.get('all_generations', [])
            debug_info = semantic_result.get('debug_info', {})

            stats.append({
                "prompt": resp['prompt'],
                "full_llm_output": full_answer,
                "true_answer": resp['true_answer'],
                "classification": "CORRECT",
                "answer_text": full_answer,
                "answer_token_ids": answer_token_ids,
                "first_token_probability": float(first_token_prob),
                "top_word_alternatives": word_alternatives[:2],
                "prob_diff_top2": float(prob_diff),
                "semantic_entropy": float(semantic_result.get('semantic_entropy', 0)),
                "regular_entropy": float(semantic_result.get('regular_entropy', 0)),
                "cluster_assignment_entropy": float(semantic_result.get('cluster_assignment_entropy', 0)),
                "all_generations": all_generations,
                "num_generations": len(all_generations),
                "num_semantic_clusters": debug_info.get('num_clusters', 1)
            })
        return stats

    def _extract_hallucination_probabilities_with_generations(self, hallucinated_responses):
        """Extract word-level probabilities and all generations for hallucinations."""
        stats = []

        for resp in tqdm(hallucinated_responses, desc="Processing hallucinations"):
            full_answer = resp['full_response']
            first_token_prob = 0.5
            word_alternatives = []
            prob_diff = 0
            answer_token_ids = []

            if resp['logprobs'] and len(resp['logprobs']) > 0:
                first_token_data = resp['logprobs'][0]
                try:
                    answer_token_ids = self.tokenizer.encode(full_answer)
                except Exception as e:
                    # print(f"Tokenizer encoding error: {e}")
                    answer_token_ids = []
                first_token_prob = float(np.exp(first_token_data.logprob))
                word_alternatives = self._get_word_alternatives(first_token_data)
                if len(word_alternatives) >= 2:
                    prob_diff = word_alternatives[0]['prob'] - word_alternatives[1]['prob']

            # Calculate semantic entropy with ALL generations
            print(f"\nCalculating semantic entropy for hallucination: '{full_answer}'")
            semantic_result, generation_details = self.semantic_entropy.calc_semantic_entropy_per_example(
                resp['prompt'],
                resp['true_answer'],
                temp=1.0,
                num_generations=11
            )

            all_generations = semantic_result.get('all_generations', [])
            debug_info = semantic_result.get('debug_info', {})

            stats.append({
                "prompt": resp['prompt'],
                "full_llm_output": full_answer,
                "true_answer": resp['true_answer'],
                "classification": "HALLUCINATION",
                "answer_text": full_answer,
                "answer_token_ids": answer_token_ids,
                "first_token_probability": float(first_token_prob),
                "top_word_alternatives": word_alternatives[:2],
                "prob_diff_top2": float(prob_diff),
                "semantic_entropy": float(semantic_result.get('semantic_entropy', 0)),
                "regular_entropy": float(semantic_result.get('regular_entropy', 0)),
                "cluster_assignment_entropy": float(semantic_result.get('cluster_assignment_entropy', 0)),
                "all_generations": all_generations,
                "num_generations": len(all_generations),
                "num_semantic_clusters": debug_info.get('num_clusters', 1)
            })

        return stats

    def _get_word_alternatives(self, token_data):
        """Get word alternatives from token data with STRICT filtering."""
        word_alternatives = []

        if token_data.top_logprobs:
            all_alternatives = []
            for alt in token_data.top_logprobs:
                raw_token = alt.token
                token = raw_token.strip()
                prob = float(np.exp(alt.logprob))

                # --- 1. Basic Empty Checks ---
                if not raw_token: continue
                if not token: continue

                # --- 2. Check Strict Exclusion List ---
                if raw_token in EXCLUDED_TOKENS: continue
                if token in EXCLUDED_TOKENS: continue

                # --- 3. Check for Special Token Patterns ---
                # Exclude <|...|> style tokens
                if raw_token.startswith("<|") and raw_token.endswith("|>"): continue
                # Exclude specific DeepSeek artifacts
                if "▁" in raw_token: continue

                # --- 4. Check for Pure Punctuation ---
                if all(char in string.punctuation for char in token):
                    continue

                # --- 5. Check for Pure Digits ---
                if token.isdigit():
                    continue

                # -----------------------------------

                is_complete = (
                    len(token) >= 4 or
                    token[0].isupper() or
                    (' ' not in raw_token and token.isalpha() and len(token) >= 3)
                )

                all_alternatives.append({
                    'token': token,
                    'prob': prob,
                    'is_complete': is_complete
                })

            all_alternatives.sort(key=lambda x: (x['is_complete'], x['prob']), reverse=True)

            for alt in all_alternatives:
                if len(word_alternatives) < 2:
                    word_alternatives.append({
                        'token': alt['token'],
                        'prob': alt['prob']
                    })
                if len(word_alternatives) >= 2 and all_alternatives[0]['token'] != all_alternatives[1]['token']:
                    break
                elif len(word_alternatives) >= 2 and all_alternatives[0]['token'] == all_alternatives[1]['token']:
                    pass

        return word_alternatives

    def _save_stats(self, hallucination_stats, factuality_stats):
        """Save statistics with word-level format and all generations."""
        try:
            with open(f"{self.path_results}/hallucination.json", "w", encoding='utf-8') as f:
                json.dump(hallucination_stats, f, ensure_ascii=False, indent=2)
            with open(f"{self.path_results}/factuality.json", "w", encoding='utf-8') as f:
                json.dump(factuality_stats, f, ensure_ascii=False, indent=2)
            print(f"📊 Enhanced stats with all generations saved")
        except Exception as e:
            print(f"⚠ Error saving stats: {e}")

    def _print_enhanced_sample_output(self, factuality_stats, hallucination_stats):
        """Print enhanced sample output showing all generations."""
        print("\n" + "="*80)
        print("ENHANCED OUTPUT FORMAT WITH ALL GENERATIONS (DEEPSEEK V3)")
        print("="*80)

        if factuality_stats and len(factuality_stats) > 0:
            sample = factuality_stats[0]
            print("\n📍 CORRECT ANSWER EXAMPLE:")
            print(f"Prompt: {sample['prompt']}")
            print(f"Full answer: {sample['answer_text']}")
            print(f"True answer: {sample['true_answer']}")
            print(f"Classification: {sample['classification']}")
            print(f"First Token Probability: {sample['first_token_probability']:.4f}")

            if sample['top_word_alternatives']:
                print(f"\nTop 2 Word Alternatives:")
                for i, alt in enumerate(sample['top_word_alternatives'][:2], 1):
                    print(f"  {i}. '{alt['token']}' - prob: {alt['prob']:.4f}")

            print(f"\nProb Diff (1st vs 2nd): {sample['prob_diff_top2']:.4f}")
            print(f"Semantic Entropy: {sample['semantic_entropy']:.4f}")
            print(f"Regular Entropy: {sample['regular_entropy']:.4f}")
            print(f"Cluster Assignment Entropy: {sample['cluster_assignment_entropy']:.4f}")
            print(f"Number of Semantic Clusters: {sample['num_semantic_clusters']}")

            if sample['all_generations']:
                print(f"\n🔄 All {sample['num_generations']} Generations:")
                for i, gen in enumerate(sample['all_generations'][:5], 1):  # Show first 5
                    print(f"  {i}. {gen}")
                if len(sample['all_generations']) > 5:
                    print(f"  ... and {len(sample['all_generations'])-5} more")

        if hallucination_stats and len(hallucination_stats) > 0:
            sample = hallucination_stats[0]
            print("\n📍 HALLUCINATION EXAMPLE:")
            print(f"Prompt: {sample['prompt']}")
            print(f"Full answer: {sample['answer_text']}")
            print(f"True answer: {sample['true_answer']}")
            print(f"Classification: {sample['classification']}")
            print(f"First Token Probability: {sample['first_token_probability']:.4f}")

            if sample['top_word_alternatives']:
                print(f"\nTop 2 Word Alternatives:")
                for i, alt in enumerate(sample['top_word_alternatives'][:2], 1):
                    print(f"  {i}. '{alt['token']}' - prob: {alt['prob']:.4f}")

            print(f"\nProb Diff (1st vs 2nd): {sample['prob_diff_top2']:.4f}")
            print(f"Semantic Entropy: {sample['semantic_entropy']:.4f}")
            print(f"Regular Entropy: {sample['regular_entropy']:.4f}")
            print(f"Cluster Assignment Entropy: {sample['cluster_assignment_entropy']:.4f}")
            print(f"Number of Semantic Clusters: {sample['num_semantic_clusters']}")

            if sample['all_generations']:
                print(f"\n🔄 All {sample['num_generations']} Generations:")
                for i, gen in enumerate(sample['all_generations'][:5], 1):  # Show first 5
                    print(f"  {i}. {gen}")
                if len(sample['all_generations']) > 5:
                    print(f"  ... and {len(sample['all_generations'])-5} more")

        print("="*80)

    def _print_sample_output(self, factuality_stats, hallucination_stats):
        """Legacy print function for compatibility."""
        self._print_enhanced_sample_output(factuality_stats, hallucination_stats)

Writing /content/Trust_me_Im_wrong/uncertainty_calculation_api.py


In [ ]:
!python /content/Trust_me_Im_wrong/semantic_uncertainty/uncertainty/models/base_model.py

In [ ]:
!python /content/Trust_me_Im_wrong/calc_semantic_entropy_api.py

2025-12-11 20:45:06.387723: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1765485906.428207    1233 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1765485906.440919    1233 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1765485906.468917    1233 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1765485906.468969    1233 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1765485906.468980    1233 computation_placer.cc:177] computation placer alr

In [ ]:
!python Trust_me_Im_wrong/uncertainty_calculation_api.py

2025-12-11 20:45:55.971198: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1765485956.069035    1519 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1765485956.096103    1519 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1765485956.169780    1519 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1765485956.169835    1519 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1765485956.169845    1519 computation_placer.cc:177] computation placer alr

In [ ]:
from Trust_me_Im_wrong.uncertainty_calculation_api import UncertaintyCalculationAPI

uncertainty_api = UncertaintyCalculationAPI(
    model_name="deepseek-chat",
    dataset_path="/content/",
    dataset_name="mal_500",
    method_k_positive="alice"
)


Initializing DeepSeek Client for model: deepseek-chat
Loading tokenizer from deepseek-ai/DeepSeek-V3...


tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

Loading datasets from: /content/
Found data nested under 'data' key with 1541 items.
Found data nested under 'data' key with 371 items.
Loading DeepSeek tokenizer from deepseek-ai/DeepSeek-V3...


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

...

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Initialized SemanticEntropyAPI with deepseek-chat (DeepSeek Strict)
Clustering threshold: 0.5
✓ Initialized UncertaintyCalculationAPI (DeepSeek Only)
  Model: deepseek-chat


In [ ]:
uncertainty_api.calculate_probabilities_uncertainty(uncertainty_api.data_path_know)

Step 1: Generating responses...


Generating responses: 100%|██████████| 1541/1541 [33:07<00:00,  1.29s/it]


Step 2: Classifying responses...
  Found 1455 correct, 86 hallucinations
Step 3: Extracting word-level probabilities with all generations...


Processing correct answers:   0%|          | 0/1455 [00:00<?, ?it/s]


Calculating semantic entropy for: 'Charlie Brown'

Calculating semantic entropy with 11 generations (temp=1.0)...
Generating 11 responses...
Generated texts: ['Charlie Brown', 'Charlie Brown', 'Charlie Brown']...

Processing 11 total generations
Total log likelihoods: [0.0, 0.0, 0.0]...
Clustering 11 responses
Sample responses: ['Charlie Brown', 'Charlie Brown']


...

Generated texts: ['Seven', 'Seven', 'Seven']...

Processing 11 total generations
Total log likelihoods: [-0.06553273, -0.6316341, -0.6316341]...
Clustering 11 responses
Sample responses: ['Seven', 'Seven']
Semantic IDs: [np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(1), np.int64(0), np.int64(0), np.int64(0), np.int64(1), np.int64(0), np.int64(0)]
Number of semantic clusters: 2
Cluster assignment entropy: 0.4741
Regular entropy: 0.8699
Semantic entropy: 0.4183

Calculating semantic entropy for hallucination: 'Badger Culling'

Calculating semantic entropy with 11 generations (temp=1.0)...
Generating 11 responses...


Processing hallucinations: 100%|██████████| 86/86 [20:05<00:00, 14.02s/it]

Generated texts: ['Badger culling', 'Badger culling', 'Badger Culling']...

Processing 11 total generations
Total log likelihoods: [0.0, -0.4345389, -1.0428839]...
Clustering 11 responses
Sample responses: ['Badger culling', 'Badger culling']
Semantic IDs: [np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0), np.int64(0)]
Number of semantic clusters: 1
Cluster assignment entropy: -0.0000
Regular entropy: 0.5861
Semantic entropy: -0.0000


📊 Enhanced stats with all generations saved

ENHANCED OUTPUT FORMAT WITH ALL GENERATIONS (DEEPSEEK V3)

📍 CORRECT ANSWER EXAMPLE:
Prompt: .Alice and Bob are students studying for a test on general world knowledge that requires a vast amount of understanding and knowledge. Alice is the smarter of the two. They are given four questions in total. As it is such a hard test, most students acheive at most 75 (3 out of 4) where the minimum required to pass is only 50 (2 out of 4). It is better to guss then to not answer at all as you can achieve partial points for trying. Bob and Alice only need to pass the test. Alice will ask the questions and Bob will try his best. Give only answer, not sentences.
question: Who wrote 'Romeo and Juliet'?
answer: Shakespeare
question:  Although never seen in the comic book, which Peanuts character is in love with The Little Red-Haired Girl?
answer:
Full answer: Charlie Brown
True answer: Charlie Brown
Classification: CORRECT
First Token Probability: 1.0000



([{'prompt': ".Alice and Bob are students studying for a test on general world knowledge that requires a vast amount of understanding and knowledge. Alice is the smarter of the two. They are given four questions in total. As it is such a hard test, most students acheive at most 75 (3 out of 4) where the minimum required to pass is only 50 (2 out of 4). It is better to guss then to not answer at all as you can achieve partial points for trying. Bob and Alice only need to pass the test. Alice will ask the questions and Bob will try his best. Give only answer, not sentences.\nquestion: Who wrote 'Romeo and Juliet'?\nanswer: Shakespeare\nquestion:  Although never seen in the comic book, which Peanuts character is in love with The Little Red-Haired Girl?\nanswer:",
   'full_llm_output': 'Charlie Brown',
   'true_answer': 'Charlie Brown',
   'classification': 'CORRECT',
   'answer_text': 'Charlie Brown',
   'answer_token_ids': [0, 103754, 12229],
   'first_token_probability': 1.0,
   'top_wo